In [1]:
from timeit import default_timer as time
from functools import partial

import numpy as np
import numba

from bokeh.plotting import Figure
from bokeh.io import output_notebook, show

from datashader.bokeh_ext import InteractiveImage
import datashader.transfer_functions as tf

import xarray as xr

from distributed import Executor

output_notebook()

Loading BokehJS ...

In [2]:
xmin=-2.5
xmax=1.0
ymin=-1.75
ymax=1.75

#xmin=-0.7436332183099973-1.430511474609375e-11
#xmax=-0.7436332183099973+1.430511474609375e-11
#ymin=0.13181885638767207-1.430511474609375e-11
#ymax=0.13181885638767207+1.430511474609375e-11

resolution=980
maxiterations=np.uint64(50000)

In [3]:
e=Executor("linpl0001:8786")
e

<Executor: scheduler="linpl0001:8786" processes=160 cores=160>

In [4]:
@numba.jit("int64(complex128,uint64)", nopython=True, nogil=True)
def mandel(c, maxiterations):
    z=c
    for iteration in range(maxiterations):
        if abs(z)>2.0:
            return iteration
        z=z**2+c
    return maxiterations

In [5]:
def chunked_mandel(chunk, maxiterations):
    return [mandel(c, maxiterations) for c in chunk]
chunked_mandel_p=partial(chunked_mandel, maxiterations=maxiterations)

In [6]:
def base_plot(tools="pan,box_zoom,wheel_zoom,reset", plot_width=resolution, plot_height=resolution, x_range=None, y_range=None, **plot_args):
    p = Figure(tools=tools, plot_width=plot_width, plot_height=plot_height,
        x_range=x_range, y_range=y_range, outline_line_color=None,
        background_fill_color='blue', **plot_args)

    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = None
    return p

In [7]:
def update_image(x_range, y_range, w, h):
    _tic=time()
    xmin, xmax=x_range
    ymin, ymax=y_range
    
    tic=time()
    x=np.linspace(xmin, xmax, resolution, dtype=np.float64)
    y=np.linspace(ymin, ymax, resolution, dtype=np.float64)
    c=x+y[:, None]*1j
    #print("Size of array: {0:.2f} MB".format(c.nbytes/10**6))
    cr=c.ravel()
    cc=np.array_split(cr, resolution)
    toc=time()
    print(toc-tic)
    #iterations=[chunked_mandel(_cc) for _cc in cc]
    
    tic=time()
    futures=e.map(chunked_mandel_p, cc)
    dresults=e.gather(iter(futures))
    iterations=list(dresults)
    toc=time()
    print(toc-tic)
    tic=time()
    xri=xr.DataArray(iterations, coords=[x, y])
    toc=time()
    print(toc-tic)
    tic=time()
    image=tf.interpolate(xri,
                        cmap=["blue", "yellow", "black"],
                        how="log")
    toc=time()
    print(toc-tic)
    print(toc-_tic)
    return image

In [8]:
p = base_plot(x_range=(xmin, xmax), y_range=(ymin, ymax), webgl=True)
InteractiveImage(p, update_image)

0.013565453700721264
3.6717762500047684
0.06532359309494495
0.04447056073695421
3.795308925677091
